In [3]:
import pandas as pd
import gspread
from oauth2client.service_account import ServiceAccountCredentials
from gspread_dataframe import get_as_dataframe
import bar_chart_race as bcr
import warnings
warnings.filterwarnings("ignore")

In [4]:
# Caminho para seu arquivo JSON com a credencial
cred_path = 'credentials.json'

# Definir escopos
scope = ['https://spreadsheets.google.com/feeds',
         'https://www.googleapis.com/auth/drive']

# Autenticação
creds = ServiceAccountCredentials.from_json_keyfile_name(cred_path, scope)
gc = gspread.authorize(creds)


# Abrir planilha e aba
spreadsheet_url = 'https://docs.google.com/spreadsheets/d/1NQ1O36AwIQk9rXCQOR7HTsnEmtegcwvVYTbpGlsco8Y/edit?gid=0#gid=0'
sh = gc.open_by_url(spreadsheet_url)
worksheet = sh.worksheet('Autos')  # ou spreadsheet.sheet1
autos = get_as_dataframe(worksheet)

# Emplacamentos
spreadsheet_url = 'https://docs.google.com/spreadsheets/d/1VHIV3gitQ-jSv479sCtILrRyrkED8V5E476P9rP-9xk/edit?gid=0#gid=0'
sh = gc.open_by_url(spreadsheet_url)
worksheet_new = sh.worksheet('Autos')
autos_new = get_as_dataframe(worksheet_new)

In [ ]:
autos = get_as_dataframe(worksheet)

In [51]:
# Passo 1: Garantir que ano_mes esteja ordenado corretamente
autos = autos.sort_values(by=['model', 'ano_mes'])

# Passo 2: Criar coluna 'periodo' no formato mm/yyyy
autos['periodo'] = autos['ano_mes'].apply(lambda x: f"{x[-2:]}/{x[:4]}")

# Passo 3: Calcular total acumulado por modelo
autos['total_acumulado'] = autos.groupby('model')['total'].cumsum()

# Passo 4: Pivot por ano_mes (para manter ordenação correta)
pivot_autos = autos.pivot_table(
    index='ano_mes',
    columns='model',
    values='total_acumulado',
    aggfunc='sum'
).ffill()

# Passo 5: Substituir o índice de ano_mes por período (mantendo a ordem!)
# Cria um dicionário de mapeamento de ano_mes para mm/yyyy
period_map = {x: f"{x[-2:]}/{x[:4]}" for x in pivot_autos.index}
pivot_autos.index = pivot_autos.index.map(period_map)

# Passo 6: Seleciona os top 20
total_vendas_por_modelo = pivot_autos.iloc[-1]
top_modelos = total_vendas_por_modelo.sort_values(ascending=False).head(20).index
pivot_autos_bcr = pivot_autos[top_modelos]
pivot_autos_bcr = pivot_autos_bcr.fillna(0)

In [52]:
pivot_autos_bcr

model          GOL        UNO      PALIO     CORSA     CELTA    FIESTA  \
ano_mes                                                                  
01/2005     80.662     43.546     32.776    37.739    10.228    11.046   
02/2005    152.333     82.724     62.130    70.458    19.427    20.931   
03/2005    240.265    130.988     99.336   111.274    31.279    33.496   
04/2005    320.716    174.719    133.629   148.200    41.999    44.681   
05/2005    403.997    219.961    167.805   185.491    52.786    56.127   
...            ...        ...        ...       ...       ...       ...   
01/2025  18981.387  10964.382  10579.315  6519.292  5733.448  4300.890   
02/2025  19039.834  10996.225  10613.089  6534.033  5753.653  4316.764   
03/2025  19094.626  11025.540  10644.216  6548.063  5772.579  4331.191   
04/2025  19159.906  11059.533  10680.470  6563.948  5794.033  4348.268   
05/2025  19227.723  11095.263  10717.882  6580.139  5816.672  4365.685   

model         FOX     SIENA   COROLLA   CLASSIC        KA     CIVIC     FUSCA  \
ano_mes                                                                         
01/2005     0.000     3.780     2.098     2.419     5.904     2.887    21.362   
02/2005     0.000     7.414     3.907     4.611    11.455     5.568    41.510   
03/2005     0.000    12.080     6.511     7.260    18.474     9.233    65.443   
04/2005     0.000    16.355     8.913     9.814    24.776    12.446    86.930   
05/2005     0.000    20.654    11.468    12.484    31.133    15.719   109.347   
...           ...       ...       ...       ...       ...       ...       ...   
01/2025  3776.845  3564.570  3227.588  3230.742  3197.363  2719.332  2526.427   
02/2025  3795.919  3579.384  3249.062  3242.951  3216.266  2732.752  2526.427   
03/2025  3813.648  3592.820  3269.180  3254.281  3233.649  2745.434  2530.379   
04/2025  3834.041  3609.109  3294.187  3267.444  3253.705  2760.907  2535.058   
05/2025  3855.030  3625.998  3320.255  3281.403  3274.440  2776.756  2539.880   

model      VOYAGE  ECOSPORT      ONIX    VECTRA   SANDERO    PARATI       FIT  
ano_mes                                                                        
01/2005     7.125     0.000     0.000    10.224     0.000    12.505     0.000  
02/2005    13.860     0.000     0.000    18.981     0.000    23.810     0.000  
03/2005    21.415     0.000     0.000    29.920     0.000    37.571     0.000  
04/2005    28.367     1.341     0.000    40.190     0.000    50.357     0.000  
05/2005    35.845     2.749     0.000    50.628     0.000    63.705     0.000  
...           ...       ...       ...       ...       ...       ...       ...  
01/2025  2380.624  2226.043  2087.453  2023.964  1886.146  1909.181  1745.335  
02/2025  2393.308  2237.291  2117.359  2028.218  1899.846  1909.181  1755.093  
03/2025  2404.919  2247.520  2144.606  2032.261  1912.519  1909.181  1764.280  
04/2025  2419.841  2259.940  2179.103  2037.007  1927.674  1909.181  1774.691  
05/2025  2435.129  2272.712  2214.651  2041.890  1943.554  1909.181  1785.697  

[242 rows x 20 columns]

In [63]:
bcr.bar_chart_race(pivot_autos_bcr, cmap='tab20')

In [68]:
autos_new

ranking            model  total  ano_mes modelo_padrao
0          1º          GM/ONIX  17463  2020_01          ONIX
1          2º     GM/ONIX PLUS   8722  2020_01     ONIX PLUS
2          3º          FORD/KA   7334  2020_01            KA
3          4º     RENAULT/KWID   6739  2020_01          KWID
4          5º     HYUNDAI/HB20   6555  2020_01          HB20
...       ...              ...    ...      ...           ...
13095     46º     NISSAN/VERSA    562  2025_05         VERSA
13096     47º    NISSAN/SENTRA    538  2025_05        SENTRA
13097     48º  TOYOTA/YARIS HB    530  2025_05      YARIS HB
13098     49º           BMW/X1    463  2025_05            X1
13099     50º       VOLVO/EX30    429  2025_05          EX30

[13100 rows x 5 columns]

In [83]:
autos_new['modelo'] = autos_new['model'].str.extract(r'/([\w\s\-]+)$')
base_novos = autos_new.copy()

base_usados = autos.copy()
base_usados['modelo'] = base_usados['model']

In [92]:
# Corrigir função de datas para evitar o erro
def calcular_total_inicio(df, meses=6):
    df = df.copy()
    df['ano'] = df['ano_mes'].str[:4].astype(int)
    df['mes'] = df['ano_mes'].str[-2:].astype(int)
    df['data'] = pd.to_datetime({'year': df['ano'], 'month': df['mes'], 'day': 1})
    
    return (
        df.sort_values('data')
          .groupby('modelo')
          .apply(lambda x: x.set_index('data')['total'].resample('MS').sum().head(meses).sum())
          .reset_index(name=f'total_{meses}_meses')
    )

# Recalcular agora com correção
total_6m = calcular_total_inicio(base_novos, 6)
total_12m = calcular_total_inicio(base_novos, 12)

# Calcular a primeira aparição nos usados
def primeira_aparicao_usado(df_usados):
    df = df_usados.copy()
    df['ano'] = df['ano_mes'].str[:4].astype(int)
    df['mes'] = df['ano_mes'].str[-2:].astype(int)
    df['data'] = pd.to_datetime({'year': df['ano'], 'month': df['mes'], 'day': 1})
    return df.groupby('modelo')['data'].min().reset_index(name='primeira_aparicao_usado')

entrada_usados = primeira_aparicao_usado(base_usados)

# Juntar as informações
resultado = total_6m.merge(total_12m, on='modelo', how='outer')
resultado = resultado.merge(entrada_usados, on='modelo', how='outer')

# Adicionar data de entrada nos novos
base_novos['ano'] = base_novos['ano_mes'].str[:4].astype(int)
base_novos['mes'] = base_novos['ano_mes'].str[-2:].astype(int)
base_novos['data'] = pd.to_datetime({'year': base_novos['ano'], 'month': base_novos['mes'], 'day': 1})
entrada_novos = base_novos.groupby('modelo')['data'].min().reset_index(name='entrada_novos')

# Combinar tudo
resultado = resultado.merge(entrada_novos, on='modelo', how='left', indicator=True)

# Calcular "vida útil" = tempo até aparecer entre os usados
resultado['meses_ate_usado'] = (
    (resultado['primeira_aparicao_usado'].dt.year - resultado['entrada_novos'].dt.year) * 12 +
    (resultado['primeira_aparicao_usado'].dt.month - resultado['entrada_novos'].dt.month)
)
resultado = resultado.sort_values('total_12_meses', ascending=False)

resultado.head(10)

modelo  total_6_meses  total_12_meses primeira_aparicao_usado  \
113        GOL        78700.0        180073.0              2005-01-01   
165      PALIO        53833.0        118756.0              2005-01-01   
159       ONIX        56498.0        118158.0              2015-01-01   
56       CELTA        52434.0        114690.0              2005-01-01   
117       HB20        53731.0        112519.0              2015-02-01   
222        UNO        38805.0         96466.0              2005-01-01   
231     VOYAGE        24642.0         73084.0              2005-01-01   
102     FIESTA        32422.0         70074.0              2005-01-01   
160  ONIX PLUS        49736.0         68007.0              2023-04-01   
223         UP        29112.0         65435.0              2018-01-01   

    entrada_novos _merge  meses_ate_usado  
113    2003-01-01   both             24.0  
165    2003-01-01   both             24.0  
159    2012-11-01   both             26.0  
56     2003-01-01   both             24.0  
117    2012-10-01   both             28.0  
222    2003-01-01   both             24.0  
231    2008-10-01   both            -45.0  
102    2003-01-01   both             24.0  
160    2019-10-01   both             42.0  
223    2014-02-01   both             47.0

In [94]:
resultado = resultado.query('_merge == "both"')

In [96]:
resultado.dropna(subset=['meses_ate_usado'], inplace=True)

In [99]:
resultado = resultado.sort_values('meses_ate_usado', ascending=False)
resultado.head(20) 

modelo  total_6_meses  total_12_meses primeira_aparicao_usado  \
218      TRACKER          565.0           843.0              2022-04-01   
107  FOCUS SEDAN         2386.0          4853.0              2020-05-01   
120    HILUX SW4         2822.0          5824.0              2020-05-01   
130        JETTA          654.0          1893.0              2019-09-01   
132     KA SEDAN        18544.0         35535.0              2023-01-01   
229        VERSA        10588.0         19292.0              2020-02-01   
112       FUSION         5082.0         11029.0              2014-04-01   
79        CRONOS        18418.0         33382.0              2025-04-01   
98   ETIOS SEDAN        13285.0         27236.0              2020-01-01   
97      ETIOS HB        11112.0         31000.0              2019-01-01   
136        KICKS        10697.0         23463.0              2022-09-01   
68    CLIO SEDAN         5168.0         13562.0              2009-03-01   
230       VIRTUS        21023.0         45143.0              2024-01-01   
45            C3         2826.0          6857.0              2009-02-01   
171   POLO SEDAN         6397.0         11627.0              2008-09-01   
220       TUCSON         1055.0          2946.0              2011-04-01   
200         SPIN        21479.0         41370.0              2017-12-01   
153         MOBI        16999.0         38764.0              2021-07-01   
82   CRUZE SEDAN        14786.0         36818.0              2016-11-01   
80     CROSS FOX        12853.0         40596.0              2008-11-01   

    entrada_novos _merge  meses_ate_usado  
218    2003-06-01   both            226.0  
107    2003-01-01   both            208.0  
120    2005-10-01   both            175.0  
130    2006-11-01   both            154.0  
132    2014-11-01   both             98.0  
229    2011-12-01   both             98.0  
112    2006-05-01   both             95.0  
79     2018-03-01   both             85.0  
98     2013-01-01   both             84.0  
97     2012-10-01   both             75.0  
136    2016-07-01   both             74.0  
68     2003-02-01   both             73.0  
230    2018-02-01   both             71.0  
45     2003-05-01   both             69.0  
171    2003-01-01   both             68.0  
220    2005-11-01   both             65.0  
200    2012-08-01   both             64.0  
153    2016-04-01   both             63.0  
82     2011-09-01   both             62.0  
80     2003-10-01   both             61.0

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# --- 1. Carregamento dos Dados (Substitua com seus DataFrames reais) ---
# Assumimos que você já tem seus DataFrames 'autos_new' e 'leves_new' ou similares.
# Para demonstração, criaremos dados fictícios.

# Dados Fictícios para Carros Novos (Jan 2003 - Mai 2025)
dates_new = pd.date_range(start='2003-01-01', end='2025-05-01', freq='MS')
models_new = ['VW/GOL', 'FIAT/PALIO', 'GM/ONIX', 'HYUNDAI/HB20', 'FORD/KA', 'VW/POLO', 'FIAT/STRADA', 'GM/CELTA', 'FIAT/UNO', 'TOYOTA/COROLLA']
data_new = []
for date in dates_new:
    for i, model in enumerate(models_new):
        total = np.random.randint(1000, 50000) / (i + 1) # Simula vendas maiores para rankings melhores
        data_new.append({'ano_mes': date.strftime('%Y_%m'), 'model': model, 'total': total, 'ranking': i + 1})
df_new_cars = pd.DataFrame(data_new)

# Dados Fictícios para Carros Usados (Jan 2005 - Mai 2025)
dates_used = pd.date_range(start='2005-01-01', end='2025-05-01', freq='MS')
models_used = ['VW/GOL', 'FIAT/PALIO', 'GM/ONIX', 'FORD/KA', 'VW/FOX', 'FIAT/UNO', 'GM/CELTA', 'VW/SAVEIRO', 'FIAT/STRADA', 'HYUNDAI/HB20'] # Alguns modelos em comum
data_used = []
for date in dates_used:
    for i, model in enumerate(models_used):
        total = np.random.randint(500, 30000) / (i + 0.5) # Simula vendas maiores para rankings melhores
        data_used.append({'ano_mes': date.strftime('%Y_%m'), 'model': model, 'total': total, 'ranking': i + 1})
df_used_cars = pd.DataFrame(data_used)

print("Cabeçalho do DataFrame de Carros Novos:")
print(df_new_cars.head())
print("\nCabeçalho do DataFrame de Carros Usados:")
print(df_used_cars.head())

# --- 2. Pré-processamento dos Dados ---

# Converter 'ano_mes' para objetos datetime para facilitar operações de tempo
df_new_cars['ano_mes_dt'] = pd.to_datetime(df_new_cars['ano_mes'], format='%Y_%m')
df_used_cars['ano_mes_dt'] = pd.to_datetime(df_used_cars['ano_mes'], format='%Y_%m')

# Garantir que 'total' seja numérico
df_new_cars['total'] = pd.to_numeric(df_new_cars['total'])
df_used_cars['total'] = pd.to_numeric(df_used_cars['total'])

# Ordenar por data e ranking
df_new_cars = df_new_cars.sort_values(by=['ano_mes_dt', 'ranking']).reset_index(drop=True)
df_used_cars = df_used_cars.sort_values(by=['ano_mes_dt', 'ranking']).reset_index(drop=True)

# --- 3. Identificar Modelos Comuns e Padronizar Nomes (Passo Crucial) ---
# Este é um passo crítico. Nomes de modelos podem variar ligeiramente entre os datasets.
# Ex: 'VW/GOL' vs 'GOL'. Você pode precisar de um mapeamento manual ou uma correspondência mais sofisticada.
# Para este exemplo, assumimos que os nomes já são consistentes o suficiente para a intersecção.

unique_new_models = set(df_new_cars['model'].unique())
unique_used_models = set(df_used_cars['model'].unique())

common_models = list(unique_new_models.intersection(unique_used_models))
print(f"\nModelos comuns encontrados: {common_models}")

# Se os nomes dos modelos forem inconsistentes, você precisaria de um mapeamento:
# model_mapping = {
#     'VW/GOL': 'GOL',
#     'FIAT/PALIO': 'PALIO',
#     # ... e assim por diante para todos os modelos que precisam de padronização
# }
# df_new_cars['model_standard'] = df_new_cars['model'].map(model_mapping).fillna(df_new_cars['model'])
# df_used_cars['model_standard'] = df_used_cars['model'].map(model_mapping).fillna(df_used_cars['model'])
# Em seguida, use 'model_standard' para a fusão.

# --- 4. Combinar os Dados ---
# Filtrar ambos os DataFrames para incluir apenas modelos comuns para uma fusão mais limpa
df_new_common = df_new_cars[df_new_cars['model'].isin(common_models)].copy()
df_used_common = df_used_cars[df_used_cars['model'].isin(common_models)].copy()

# Renomear colunas para evitar conflitos após a fusão
df_new_common = df_new_common.rename(columns={'total': 'new_total', 'ranking': 'new_ranking'})
df_used_common = df_used_common.rename(columns={'total': 'used_total', 'ranking': 'used_ranking'})

# Realizar a fusão (merge)
# Usamos 'inner' merge para manter apenas os registros onde um modelo existe em ambos os datasets para aquele mês
merged_df = pd.merge(
    df_new_common,
    df_used_common,
    on=['ano_mes_dt', 'model'],
    how='inner',
    suffixes=('_new', '_used')
)

# Filtrar para o período de sobreposição dos dados (Jan 2005 - Mai 2025)
merged_df = merged_df[(merged_df['ano_mes_dt'] >= '2005-01-01') & (merged_df['ano_mes_dt'] <= '2025-05-01')]

print("\nCabeçalho do DataFrame Combinado (Modelos Comuns e Datas Sobrepostas):")
print(merged_df.head())
print(f"Total de registros no DataFrame combinado: {len(merged_df)}")

# --- 5. Análise ---

print("\n--- Análise: Impacto do Volume de Vendas de Carros Novos nos Rankings de Usados ---")

# A. Correlação entre Volumes de Vendas de Novos e Usados (Simultânea)
print("\nCorrelação entre Volumes de Vendas de Novos e Usados (Simultânea):")
correlation_simultaneous = merged_df['new_total'].corr(merged_df['used_total'])
print(f"Coeficiente de correlação de Pearson: {correlation_simultaneous:.2f}")
if correlation_simultaneous > 0.5:
    print("Interpretação: Há uma forte correlação positiva. Maiores vendas de novos tendem a coincidir com maiores vendas de usados para o mesmo modelo no mesmo mês.")
elif correlation_simultaneous > 0.2:
    print("Interpretação: Há uma correlação positiva moderada.")
else:
    print("Interpretação: Há uma correlação fraca ou não significativa.")

# B. Correlação com Atraso (Lagged Correlation)
# Vamos verificar para atrasos de 1, 3 e 6 meses.
print("\nCorrelação com Atraso (Vendas de Novos vs. Vendas Futuras de Usados):")
lags = [1, 3, 6] # em meses

for lag in lags:
    # Criar uma coluna 'new_total' com atraso
    # Agrupar por modelo para garantir que o atraso seja calculado dentro da série temporal de cada modelo
    merged_df[f'new_total_lag_{lag}'] = merged_df.groupby('model')['new_total'].shift(lag)
    
    # Calcular a correlação, descartando NaNs introduzidos pelo shift
    lagged_correlation = merged_df['used_total'].corr(merged_df[f'new_total_lag_{lag}'])
    print(f"Correlação (Vendas de Novos {lag} meses atrás vs. Vendas Atuais de Usados): {lagged_correlation:.2f}")

# C. Comparação de Ranking Médio
print("\nComparação de Ranking Médio (Novos vs. Usados):")
avg_rankings = merged_df.groupby('model')[['new_ranking', 'used_ranking']].mean().sort_values(by='new_ranking')
print(avg_rankings)
# Interpretação: Se 'new_ranking' for consistentemente menor (melhor) que 'used_ranking',
# significa que o modelo é geralmente mais popular como carro novo do que como usado.
# Se forem similares, sugere popularidade consistente.

# D. Presença dos Modelos Top de Novos nos Rankings de Usados
print("\nPresença e Ranking Médio de Usados dos Modelos Top de Novos:")
# Obter os 5 modelos top de novos (pela média de vendas)
top_new_models_overall = df_new_cars.groupby('model')['total'].mean().nlargest(5).index.tolist()
print(f"Top 5 Modelos de Carros Novos (por Volume Médio de Vendas): {top_new_models_overall}")

# Para esses modelos top de novos, vamos ver seu ranking médio de usados
top_new_in_used_rankings = merged_df[merged_df['model'].isin(top_new_models_overall)].groupby('model')['used_ranking'].mean().sort_values()
print("\nRanking Médio de Usados para esses Modelos Top de Novos:")
print(top_new_in_used_rankings)

# E. Visualização (para alguns modelos-chave)
print("\n--- Visualização das Tendências de Vendas para Modelos Chave ---")
# Selecionar alguns modelos para visualizar
models_to_plot = common_models[:3] # Plotar os 3 primeiros modelos comuns

plt.figure(figsize=(15, 7))
for model in models_to_plot:
    model_data = merged_df[merged_df['model'] == model].set_index('ano_mes_dt')
    if not model_data.empty:
        plt.plot(model_data.index, model_data['new_total'], label=f'{model} - Novos', marker='o', markersize=2)
        plt.plot(model_data.index, model_data['used_total'], label=f'{model} - Usados', marker='x', markersize=2)

plt.title('Volume de Vendas de Carros Novos vs. Usados ao Longo do Tempo')
plt.xlabel('Data')
plt.ylabel('Volume de Vendas')
plt.legend()
plt.grid(True)
plt.tight_layout()
plt.show()

print("\n--- Visualização das Tendências de Ranking para Modelos Chave ---")
plt.figure(figsize=(15, 7))
for model in models_to_plot:
    model_data = merged_df[merged_df['model'] == model].set_index('ano_mes_dt')
    if not model_data.empty:
        plt.plot(model_data.index, model_data['new_ranking'], label=f'{model} - Ranking Novos', marker='o', markersize=2)
        plt.plot(model_data.index, model_data['used_ranking'], label=f'{model} - Ranking Usados', marker='x', markersize=2)

plt.title('Ranking de Carros Novos vs. Usados ao Longo do Tempo (Menor é Melhor)')
plt.xlabel('Data')
plt.ylabel('Ranking')
plt.legend()
plt.grid(True)
plt.gca().invert_yaxis() # Inverter o eixo Y para que rankings menores (melhores) fiquem no topo
plt.tight_layout()
plt.show()

print("\n--- Conclusão Preliminar ---")
print("A análise de correlação e os gráficos podem indicar se há uma relação direta entre o volume de vendas de carros novos e os rankings de usados.")
print("Uma correlação positiva entre 'new_total' e 'used_total' (especialmente com um pequeno atraso) sugere que modelos populares como novos tendem a ser populares como usados.")
print("A comparação dos rankings médios e a presença de modelos top de novos nos rankings de usados reforçam essa ideia.")
print("No entanto, é importante notar que fatores como durabilidade, custo de manutenção, valor de revenda e demanda específica do mercado de usados também influenciam a popularidade de um modelo no mercado de usados.")
print("O exemplo do 'VW/GOL' ser 1º colocado entre os usados por muito tempo, mesmo não sendo sempre o 1º novo, indica que a popularidade no mercado de usados pode ser uma combinação complexa de volume de novos (oferta) e outros fatores (demanda, reputação, etc.).")
